# Bhattachryya Distances Validation
* [Plotly](https://plot.ly/)
* [Bhattacharyya](https://en.wikipedia.org/wiki/Bhattacharyya_distance)

In [9]:
import Recovery_RL_Agent
import env_robot
import numpy as np
# import torch
import region


robot = env_robot.Env(dim=2)
agent = Recovery_RL_Agent.Agent()


goal_array = np.array(([100,300],[100,500],[300,500],[300,300],[300,200],[300,100]))
demo_act_dict = agent.demo_record(goal_array)
robot.demonstration(goal_array)
repeat_times = 100
robot.demonstration(goal_array)

for i in range(0,repeat_times):
    # executing the demo action and restore experience tuples in agent
    episode_record = robot.execute_demo_act(demo_act_dict)
    agent.exp_record(episode_record)
    # Reset env, back to start point
    robot.test_reset()


experience_list = agent.get_exp_list()

print(experience_list)

Agent: agent has recorded the demonstration as its original skills: OrderedDict([('0', array([100, 300])), ('1', array([100, 500])), ('2', array([300, 500])), ('3', array([300, 300])), ('4', array([300, 200])), ('5', array([300, 100]))]) 

Agent: agent  recorded the final goal state as : [300 100] 

Env: the original demonstration skills amount is:6 

Env: The demonstration is:
point 0: [100 300]
point 1: [100 500]
point 2: [300 500]
point 3: [300 300]
point 4: [300 200]
point 5: [300 100]
Env: The final goal position is:[300 100]

Env: The final action goal is:[300 100]

Env: the original demonstration skills amount is:6 

Env: The demonstration is:
point 0: [100 300]
point 1: [100 500]
point 2: [300 500]
point 3: [300 300]
point 4: [300 200]
point 5: [300 100]
Env: The final goal position is:[300 100]

Env: The final action goal is:[300 100]

[Experience(state=array([0., 0., 0., 0., 0., 0.]), action={'0': array([100, 300])}, reward=-379.47331922020555, next_state=array([100., 300.,  

In [10]:
import numpy as np
import clustering
import matplotlib.pyplot as plt

# s1 = np.random.uniform(0, 8, (100,2))
# s2 = np.random.uniform(2, 18, (100,2))
# s3 = np.random.uniform(30, 40, (100,2))

s1 = []
s2 = []
for e in experience_list:
    s1.append(e.state)
for e in experience_list:
    s2.append(e.next_state)
    
def extract_xy(input_set):
    x=[]
    y=[]
    for i in range(len(input_set)):
        x.append(input_set[i][0])
        y.append(input_set[i][1])
    return x,y

        

In [11]:
import plotly.graph_objs as go
import plotly.plotly as py
import plotly

## Step 1. Two-D Scatter of random points

In [12]:
s1_x,s1_y = extract_xy(s1)
s2_x,s2_y = extract_xy(s2)

trace1 = go.Scatter(
    x=s1_x,
    y=s1_y,
    name='Current State',
    mode='markers',
    # Point size color and transparency
    marker=dict(
        size=7,
        # Point outline color and width
        line=dict(
            color='rgba(217, 217, 217, 0.14)',
            width=0.5
        ),
        opacity=0.9
    )
)

# s2 setting
trace2 = go.Scatter(
    x=s2_x,
    y=s2_y,
    name='Next State',
    mode='markers',
    marker=dict(
        color='rgba(204, 10, 20)',
        size=7,
        symbol='circle',
        line=dict(
            color='rgb(204, 10, 20)',
            width=1
        ),
        opacity=0.7
    )
)

trace3 = go.Scatter(
    x=s2_x,
    y=s2_y,
    name='Action',
    mode='lines',
    line=dict(color='rgb(125,125,125)', width=1),
    opacity=0.9
)


# data = [trace1, trace2, trace3]
data = [trace1, trace2, trace3]

layout = go.Layout(
    title='2D Scatter of 3 random sets',
#     margin=dict(
#         l=0,
#         r=0,
#         b=0,
#         t=0
#     )
)
fig = go.Figure(data=data, layout=layout)
plotly.offline.init_notebook_mode()
plotly.offline.iplot(fig)

## Step 2. Calculate the related distribution

In [13]:
mean_s1 = np.mean(s1, axis=0)
cov_s1 = np.cov(s1.T)
distribution_s1 = [mean_s1, cov_s1]

mean_s2 = np.mean(s2, axis=0)
cov_s2 = np.cov(s2.T)
distribution_s2 = [mean_s2, cov_s2]


mean_s3 = np.mean(s3, axis=0)
cov_s3 = np.cov(s3.T)
distribution_s3 = [mean_s3, cov_s3]

AttributeError: 'list' object has no attribute 'T'

In [ ]:
def bhat_distance(obs_a, obs_b):
    """Caculate the Bhattacharyya Distance of every oberservations in point
    Reference
    ---------
    https://en.wikipedia.org/wiki/Bhattacharyya_distance
    """
    if not len(obs_a) == len(obs_b):
        raise ValueError("a and b must be of the same size")
    DIFF = np.array(obs_a[0])-np.array(obs_b[0])
    SUM = (np.array(obs_a[1])+np.array(obs_b[1]))*0.5
    DET = np.linalg.det(SUM)/np.sqrt(np.linalg.det(np.array(obs_a[1]))* \
    np.linalg.det(np.array(obs_b[1])))
    return 0.125*np.dot(np.dot(DIFF, np.linalg.inv(SUM)), DIFF.T) + \
         0.5*np.log10(DET)

## Step 3. Return the Bhattacharyya Distance of each Distribution

In [ ]:
d12 = bhat_distance(distribution_s1, distribution_s2)
d13 = bhat_distance(distribution_s1, distribution_s3)
d23 = bhat_distance(distribution_s2, distribution_s3)

print('Bhattacharyya Distances Between s1 and s2: ', d12)
print('Bhattacharyya Distances Between s1 and s3: ', d13)
print('Bhattacharyya Distances Between s2 and s3: ', d23)


### Step 3. Three-D Graph with Probability Density

In [ ]:
from scipy.stats import multivariate_normal
rv_s1 = multivariate_normal(mean_s1, cov_s1)
rv_s2 = multivariate_normal(mean_s2, cov_s2)
rv_s3 = multivariate_normal(mean_s3, cov_s3)

In [ ]:
def convert(distribution, size):
    """Convert distribution to z axis value
    Parameters
    ----------
    distribution : class 'scipy.stats._multivariate.multivariate_normal_frozen'
        multivariate_normal
    size : int
        the mesh size
    """
    x = np.linspace(0, size, 100)
    y = np.linspace(0, size, 100)
    point = []
    Z = []
    for i in range(len(x)):
        a = []
        for j in range(len(y)):
            a.append([x[i],y[j]])
        point.append(a)
        b = distribution.pdf(a)
        Z.append(b)
    return Z

In [ ]:
z1 = convert(rv_s1, 50)
z2 = convert(rv_s2, 50)
z3 = convert(rv_s3, 50)

# data = [go.Surface(z=Z1, colorscale='Viridis')]

data = [
    go.Surface(z=z1, colorscale='Viridis'),
    go.Surface(z=z2, colorscale='Viridis', showscale=False, opacity=0.9),
    go.Surface(z=z3, colorscale='Viridis', showscale=False, opacity=0.9)

]
layout = go.Layout(
    width=800,
    height=900,
    autosize=False,
    margin=dict(t=0, b=0, l=0, r=0),
    scene=dict(
        xaxis=dict(
            gridcolor='rgb(255, 255, 255)',
            zerolinecolor='rgb(255, 255, 255)',
            showbackground=True,
            backgroundcolor='rgb(230, 230,230)'
        ),
        yaxis=dict(
            gridcolor='rgb(255, 255, 255)',
            zerolinecolor='rgb(255, 255, 255)',
            showbackground=True,
            backgroundcolor='rgb(230, 230, 230)'
        ),
        zaxis=dict(
            gridcolor='rgb(255, 255, 255)',
            zerolinecolor='rgb(255, 255, 255)',
            showbackground=True,
            backgroundcolor='rgb(230, 230,230)'
        ),
        aspectratio = dict(x=1, y=1, z=0.7),
        aspectmode = 'manual'
    )
)

updatemenus=list([
    dict(
        buttons=list([   
            dict(
                args=['type', 'surface'],
                label='3D Surface',
                method='restyle'
            ),
            dict(
                args=['type', 'heatmap'],
                label='Heatmap',
                method='restyle'
            )             
        ]),
        direction = 'down',
        pad = {'r': 10, 't': 10},
        showactive = True,
        x = 0.1,
        xanchor = 'left',
        y = 1.1,
        yanchor = 'top' 
    ),
])

annotations = list([
    dict(text='Trace type:', x=0, y=1.085, yref='paper', align='left', showarrow=False)
])
layout['updatemenus'] = updatemenus
layout['annotations'] = annotations

fig = dict(data=data, layout=layout)
plotly.offline.init_notebook_mode()
plotly.offline.iplot(fig)

In [ ]:
# s1 setting
trace1 = go.Scatter3d(
    x=s1[:,0],
    y=s1[:,1],
    z=rv_s1.pdf(s1),
    mode='markers',
    # Point size color and transparency
    marker=dict(
        size=7,
        # Point outline color and width
        line=dict(
            color='rgba(217, 217, 217, 0.14)',
            width=0.5
        ),
        opacity=0.8
    )
)

trace_11 = go.Mesh3d(
    x=s1[:,0],
    y=s1[:,1],
    z=rv_s1.pdf(s1),
    color='#00B5FD',
    opacity=0.50
)

# s2 setting
trace2 = go.Scatter3d(
    x=s2[:,0],
    y=s2[:,1],
    z=rv_s2.pdf(s2),
    mode='markers',
    marker=dict(
        color='rgba(204, 10, 20)',
        size=7,
        symbol='circle',
        line=dict(
            color='rgb(204, 10, 20)',
            width=1
        ),
        opacity=0.9
    )
)
    
trace_22 = go.Mesh3d(
    x=s2[:,0],
    y=s2[:,1],
    z=rv_s2.pdf(s2),
    color='#00fd86',
    opacity=0.50
)

# s3 setting
trace3 = go.Scatter3d(
    x=s3[:,0],
    y=s3[:,1],
    z=rv_s3.pdf(s3),
    mode='markers',
    marker=dict(
        color='rgba(20, 100, 200)',
        size=7,
        symbol='circle',
        line=dict(
            color='rgb(20, 100, 200)',
            width=1
        ),
        opacity=0.9
    )
)
trace_33 = go.Mesh3d(
    x=s3[:,0],
    y=s3[:,1],
    z=rv_s3.pdf(s3),
    color='#b100fd',
    opacity=0.50
)

data = [trace1, trace_11, trace2, trace_22, trace3, trace_33]
layout = go.Layout(
    title='3D Scatter of 3 random sets',
    margin=dict(
        l=0,
        r=0,
        b=0,
        t=0
    )
)
fig = go.Figure(data=data, layout=layout)
# py.offline.iplot(fig)# offline plot
plotly.offline.init_notebook_mode()
plotly.offline.iplot(fig)